# Your first scraper
In this project, we will guide you step by step through the process of:

1. creating a self-contained development environment.
1. retrieving some information from an API (a website for computers)
2. leveraging it to scrape a website that does not provide an API
3. saving the output for later processing

Here we query an API for a list of countries and their past leaders. We then extract and sanitize their short bio from Wikipedia. Finally, we save the data to disk.

This task is often the first (coding) step of a datascience project and you will often come back to it in the future.

You will study topics such as *scraping*, *data structures*, *regular expressions*, *concurrency* and *file handling*. We will point out useful resources at the appropriate time. 

Let's dive in!

## API Scraping

### A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword.

NOTE: external libraries need to be installed first. Check their documentation.

Check the [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the Requests documentation to:
1. use the `get()` method to connect to this endpoint: https://country-leaders.herokuapp.com/status
2. check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is the signification of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


## Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper`.

You will find more info about virtual environments [here](../2.python/1.python_fundamentals/02.Package-Managers/00.Package_Managers.md).

Activate it.

In [127]:
import requests

# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = "https://country-leaders.herokuapp.com"

# assign the /status endpoint to another variable called status_url (1 line)
status_url = "/status"
# query the /status endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(root_url + status_url)
# check the status_code using a condition and print appropriate messages (4 lines)
if req.status_code == requests. codes.ok:
    print(f"all good\ncode is {req.status_code}")
else:
    print ("not good")

all good
code is 200


### Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. Check what to do in the Requests [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/).


In [128]:
# Set the country_url variable (1 line)
country_url ="/countries"

# query the /country endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(root_url + status_url)
# Get the JSON content and store it in the countries variable (1 line)
countries = req.json()
# display the request's status code and the countries variable (1 line)
print(countries)


Alive


### Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [129]:
# Set the cookie_url variable (1 line)
cookie_url = root_url + "/cookie"
# Query the enpoint, set the cookies variable and display it (3 lines)
def new_cookies():
   r = requests.get(cookie_url)
   return r.cookies
      
new_cookies ()


<RequestsCookieJar[Cookie(version=0, name='user_cookie', value='f7c3c4be-3775-4da6-8d68-9224f1310304', port=None, port_specified=False, domain='country-leaders.herokuapp.com', domain_specified=False, domain_initial_dot=False, path='/', path_specified=True, secure=False, expires=None, discard=True, comment=None, comment_url=None, rest={'SameSite': 'lax'}, rfc2109=False)]>

Try to query the countries endpoint using the cookie, save the output and print it.

In [130]:
# query the /countries endpoint, assign the output to the countries variable (1 line)
countries = root_url + "/countries"
# and check the status code and the countries variable's content (3 lines)
cookies = new_cookies()
req_countries = requests.get (countries, cookies=cookies)
print(req_countries.status_code)
print(req_countries.json())


200
['be', 'fr', 'us', 'ma', 'ru']


Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### Getting the actual data from the API

Query the `/leaders` endpoint.

In [131]:
# query the /leaders endpoint, assign the output to the leaders variable (1 line)
leaders = root_url + "/leaders"
# and check its content (4 lines)
cookies = new_cookies()
payload = {'country':'fr'}
req = requests.get(leaders, params=payload, cookies=cookies)
print(req.json())

[{'id': 'Q157', 'first_name': 'François', 'last_name': 'Hollande', 'birth_date': '1954-08-12', 'death_date': None, 'place_of_birth': 'Rouen', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Hollande', 'start_mandate': '2012-05-15', 'end_mandate': '2017-05-14'}, {'id': 'Q329', 'first_name': 'Nicolas', 'last_name': 'Sarkozy', 'birth_date': '1955-01-28', 'death_date': None, 'place_of_birth': 'Paris', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Nicolas_Sarkozy', 'start_mandate': '2007-05-16', 'end_mandate': '2012-05-15'}, {'id': 'Q2038', 'first_name': 'François', 'last_name': 'Mitterrand', 'birth_date': '1916-10-26', 'death_date': '1996-01-08', 'place_of_birth': 'Jarnac', 'wikipedia_url': 'https://fr.wikipedia.org/wiki/Fran%C3%A7ois_Mitterrand', 'start_mandate': '1981-05-21', 'end_mandate': '1995-05-17'}, {'id': 'Q2042', 'first_name': 'Charles', 'last_name': 'de Gaulle', 'birth_date': '1890-11-22', 'death_date': '1970-11-09', 'place_of_birth': 'Lille', 'wikipedia_url': 'h

It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.herokuapp.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [132]:
# Set the leaders_url variable (1 line)

# query the /leaders endpoint using cookies and parameters (take any country in countries)
# check the result (3 lines) 


### A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each entry in a dictionary called `leaders_per_country` like this one: 
`{'fr':[{leader0}, {leader1},...],
'en':[{leader0}, {leader1},...],
...
}`.

In [133]:
# 5 lines
leaders_per_country ={}
cookies = new_cookies()
for country in req_countries.json():
    payload = {'country':country}
    req = requests.get(leaders, params=payload, cookies=cookies)
    leaders_per_country[country] = req.json()

print(leaders_per_country)
    


{'be': [{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'}, {'id': 'Q12983', 'first_name': 'Herman', 'last_name': 'Van Rompaey', 'birth_date': '1947-10-31', 'death_date': None, 'place_of_birth': 'Etterbeek', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Herman_Van_Rompuy', 'start_mandate': '2008-12-30', 'end_mandate': '2009-11-25'}, {'id': 'Q14989', 'first_name': 'Léon', 'last_name': 'Delacroix', 'birth_date': '1867-12-27', 'death_date': '1929-10-15', 'place_of_birth': 'Saint-Josse-ten-Noode', 'wikipedia_url

It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [134]:
# 15 lines
def get__leaders():
  root_url = "https://country-leaders.herokuapp.com"
  leaders = root_url + "/leaders"
  cookie_url = root_url + "/cookie"
  def new_cookies():
     r = requests.get(cookie_url)
     return r.cookies

  countries = root_url + "/countries"
  cookies = new_cookies()
  req_countries = requests.get (countries, cookies=cookies)
  leaders_per_country ={}
  for country in req_countries.json():
     payload = {'country':country}
     req = requests.get(leaders, params=payload, cookies=cookies)
     leaders_per_country[country] = req.json()

     
     return leaders_per_country
  


Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [135]:
# 2 lines
leaders_per_country = get__leaders()
print(leaders_per_country)


{'be': [{'id': 'Q12978', 'first_name': 'Guy', 'last_name': 'Verhofstadt', 'birth_date': '1953-04-11', 'death_date': None, 'place_of_birth': 'Dendermonde', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt', 'start_mandate': '1999-07-12', 'end_mandate': '2008-03-20'}, {'id': 'Q12981', 'first_name': 'Yves', 'last_name': 'Leterme', 'birth_date': '1960-10-06', 'death_date': None, 'place_of_birth': 'Wervik', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme', 'start_mandate': '2009-11-25', 'end_mandate': '2011-12-06'}, {'id': 'Q12983', 'first_name': 'Herman', 'last_name': 'Van Rompaey', 'birth_date': '1947-10-31', 'death_date': None, 'place_of_birth': 'Etterbeek', 'wikipedia_url': 'https://nl.wikipedia.org/wiki/Herman_Van_Rompuy', 'start_mandate': '2008-12-30', 'end_mandate': '2009-11-25'}, {'id': 'Q14989', 'first_name': 'Léon', 'last_name': 'Delacroix', 'birth_date': '1867-12-27', 'death_date': '1929-10-15', 'place_of_birth': 'Saint-Josse-ten-Noode', 'wikipedia_url

## Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [136]:
# 3 lines
import requests
req = requests.get('https://fr.wikipedia.org/wiki/Emmanuel_Macron')
req.text



'<!DOCTYPE html>\n<html class="client-nojs" lang="fr" dir="ltr">\n<head>\n<meta charset="UTF-8"/>\n<title>Emmanuel Macron — Wikipédia</title>\n<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\\t.","\xa0\\t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","janvier","février","mars","avril","mai","juin","juillet","août","septembre","octobre","novembre","décembre"],"wgRequestId":"d3096c99-95ac-4015-b040-7834084e1cea","wgCSPNonce":false,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Emmanuel_Macron","wgTitle":"Emmanuel Macron","wgCurRevisionId":197054612,"wgRevisionId":197054612,"wgArticleId":6298771,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Article contenant un lien mort","Page dont la protection est à vérifier","Page en semi-protection étendue","Page au nom protégé","A

In [137]:
# 3 lines
from bs4 import BeautifulSoup
import html
soup = BeautifulSoup(req.text, "html.parser")
print(soup.prettify())







<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="fr">
 <head>
  <meta charset="utf-8"/>
  <title>
   Emmanuel Macron — Wikipédia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":false,"wgSeparatorTransformTable":[",\t."," \t,"],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","janvier","février","mars","avril","mai","juin","juillet","août","septembre","octobre","novembre","décembre"],"wgRequestId":"d3096c99-95ac-4015-b040-7834084e1cea","wgCSPNonce":false,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":false,"wgNamespaceNumber":0,"wgPageName":"Emmanuel_Macron","wgTitle":"Emmanuel Macron","wgCurRevisionId":197054612,"wgRevisionId":197054612,"wgArticleId":6298771,"wgIsArticle":true,"wgIsRedirect":false,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Article contenant un lien mort","Page dont la protection est à vérifier","Page en semi-protection étendue","Page au nom prot

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [138]:
# 2 lines

paragraphs = soup.find_all('p')
print(f"page has {len(paragraphs)} paragraphs")
print(paragraphs[1])





page has 213 paragraphs
<p class="sidebar-toc-title">
				Sommaire
				<button class="vector-toc-uncollapse-button">déplacer vers la barre latérale</button>
<button class="vector-toc-collapse-button">masquer</button>
</p>


If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one
  * store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
  * exit the loop

In [139]:
# 6 lines
for paragraph in soup.find_all('p'):
    if paragraph.find('b'):
      first_paragraph = paragraph.text
      break
print(first_paragraph)    
    

Emmanuel Macron (/ɛmanɥɛl makʁɔ̃/[e] Écouter), né le 21 décembre 1977 à Amiens (France), est un haut fonctionnaire et homme d'État français. Il est président de la République française depuis le 14 mai 2017.



At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [140]:
# 10 lines
# def get_first_paragraph(wikipedia_url):
   
def get_first_paragraph(wikipedia_url):
    #   print(wikipedia_url) # keep this for the rest of the notebook
      print(wikipedia_url)
#   [insert your code]
      from bs4 import BeautifulSoup
      import html
      soup = BeautifulSoup(req.text, "html.parser")
      paragraphs = soup.find_all('p')
      for paragraph in soup.find_all('p'):
         if paragraph.find('b'):
            first_paragraph = paragraph.text
            break
      
#   return first_paragraph
      return first_paragraph

get_first_paragraph('https://fr.wikipedia.org/wiki/Emmanuel_Macron')

https://fr.wikipedia.org/wiki/Emmanuel_Macron


"Emmanuel Macron (/ɛmanɥɛl makʁɔ̃/[e] Écouter), né le 21 décembre 1977 à Amiens (France), est un haut fonctionnaire et homme d'État français. Il est président de la République française depuis le 14 mai 2017.\n"

### Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [141]:
# 4 lines
import re
#regex = "\[\d+\]"
regexpaterns = ["\[\d+\]","\[\w\]","\([^)]*\)"]
ntext = ''

text = get_first_paragraph('https://fr.wikipedia.org/wiki/Emmanuel_Macron')
#text = re.sub(regex,'',text)
#print (text)
for regex in regexpaterns:
    ntext = re.sub(regex,'',text)

print(ntext)

https://fr.wikipedia.org/wiki/Emmanuel_Macron
Emmanuel Macron , né le 21 décembre 1977 à Amiens , est un haut fonctionnaire et homme d'État français. Il est président de la République française depuis le 14 mai 2017.



Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [142]:
# 10 lines
import re
from bs4 import BeautifulSoup
import html

def get_first_paragraph(wikipedia_url):
     print(wikipedia_url) # keep this for the rest of the notebook
          
          #   [insert your code]
     soup = BeautifulSoup(req.text, "html.parser")
     paragraphs = soup.find_all('p')
     for paragraph in soup.find_all('p'):
          if paragraph.find('b'):
               first_paragraph = paragraph.text
               break
          
     regex = "\[\d+\]"
     first_paragraph = re.sub(regex,'',first_paragraph)
     print (first_paragraph)
               #   return first_paragraph
     return first_paragraph
     
get_first_paragraph('https://fr.wikipedia.org/wiki/Emmanuel_Macron')

https://fr.wikipedia.org/wiki/Emmanuel_Macron
Emmanuel Macron (/ɛmanɥɛl makʁɔ̃/[e] Écouter), né le 21 décembre 1977 à Amiens (France), est un haut fonctionnaire et homme d'État français. Il est président de la République française depuis le 14 mai 2017.



"Emmanuel Macron (/ɛmanɥɛl makʁɔ̃/[e] Écouter), né le 21 décembre 1977 à Amiens (France), est un haut fonctionnaire et homme d'État français. Il est président de la République française depuis le 14 mai 2017.\n"

Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [143]:
# 10 lines
from curses.panel import new_panel
import re
from bs4 import BeautifulSoup
import html

def get_first_paragraph(wikipedia_url):
     # initialization variables
     req = requests.get(wikipedia_url)
     soup = BeautifulSoup(req.text, "html.parser")
     paragraphs = soup.find_all('p')
     regexpaterns = ["\[\d+\]","\[\w\]","\([^)]*\)"]
     new_paragraph = ''

     #print(wikipedia_url) # keep this for the rest of the notebook
          
          #   [insert your code]
     
     for paragraph in soup.find_all('p'):
          if paragraph.find('b'):
               first_paragraph = paragraph.text
               break
               
     for regex in regexpaterns:
          new_paragraph = re.sub(regex,'',first_paragraph)
     
     return new_paragraph

get_first_paragraph('https://fr.wikipedia.org/wiki/Emmanuel_Macron')

"Emmanuel Macron , né le 21 décembre 1977 à Amiens , est un haut fonctionnaire et homme d'État français. Il est président de la République française depuis le 14 mai 2017.\n"

### Caching
Good job! This function will be called many times. First because there are many leaders to loop through. Second because you are developing your code and are likely to re-run your loop multiple times. Third because the API might change and contain new leaders and you might want to update your data periodically.

For all these reasons, it can be benificial to *cache* the result of the `get_first_paragraph()` function so that if it called with the same parameter, you expect the same output and thus do not need to query Wikipedia another time.

You will use the [lru_cache](https://docs.python.org/3/library/functools.html#functools.lru_cache) decorator from the `functools` module. It is a tiny code change that will speed things up big time. You can use a `maxsize` of None. If you have questions about decorators, you will find more information [here](../../2.python/2.python_advanced/07.Decorator/decorators.ipynb)

In [144]:
# < 20 lines
from functools impor
@lru_cache(maxsize=None)

  



SyntaxError: invalid syntax (887290190.py, line 2)

Let's check the speedup!

In [ ]:
%%timeit
get_first_paragraph(wikipedia_url)

## Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [145]:
# 19 lines
def get__leaders():
  root_url = "https://country-leaders.herokuapp.com"
  
  cookie_url = root_url + "/cookie"
  cookies = requests.get(cookie_url).cookies

  countries_url = root_url + "/countries"
  req_countries = requests.get (countries_url, cookies=cookies)
  countries = req_countries.json()
  
  leaders_url = root_url + "/leaders"
  leaders_per_country ={}

  for country in countries:
     payload = {'country':country}
     req_leaders = requests.get(leaders_url, params=payload, cookies=cookies)
     leaders_per_country[country] = req_leaders.json()
     
     if req_leaders.status_code ==403:
           cookies = requests.get(cookie_url).cookies
           req_leaders = requests.get(leaders_url, params=payload, cookies=cookies)
     leaders = req_leaders.json()
      
     for leader in leaders:
            leader["first_paragraph"] = get_first_paragraph(leader["wikipedia_url"])
     leaders_per_country[country] = leaders
      
     return leaders_per_country


    

get__leaders()



{'be': [{'id': 'Q12978',
   'first_name': 'Guy',
   'last_name': 'Verhofstadt',
   'birth_date': '1953-04-11',
   'death_date': None,
   'place_of_birth': 'Dendermonde',
   'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt',
   'start_mandate': '1999-07-12',
   'end_mandate': '2008-03-20',
   'first_paragraph': 'Guy Maurice Marie-Louise Verhofstadt[5] )  is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten . Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Nu is hij lid van het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa  was.[6]\n'},
  {'id': 'Q12981',
   'first_name': 'Yves',
   'last_name': 'Leterme',
   'birth_date': '1960-10-06',
   'death_date': None,
   'place_of_birth': 'Wervik',
   'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme',
   'start_mandate': '2009-11-25',
   'end_mandate': '2011-12-06',
   'first_paragraph': 'Yves Cami

In [ ]:
# Check the output of your function (2 lines)


Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function to check if the `status_code` is a cookie error. In which case, get new ones and query the api again.

If not, you may have a fast connection or a bit of luck. Do it anyway.

In [154]:
# 22 lines
def get_first_paragraph(wikipedia_url, session):
     # initialization variables
     req = session.get(wikipedia_url)
     soup = BeautifulSoup(req.text, "html.parser")
     paragraphs = soup.find_all('p')
     regexpaterns = ["\[\d+\]","\[\w\]","\([^)]*\)"]
     new_paragraph = ''

     print(wikipedia_url) # keep this for the rest of the notebook
          
          #   [insert your code]
     
     for paragraph in soup.find_all('p'):
          if paragraph.find('b'):
               first_paragraph = paragraph.text
               break
               
     for regex in regexpaterns:
          first_paragraph = re.sub(regex,'',first_paragraph)
     
     return first_paragraph

Check the output of your function again.

In [ ]:
%%time
# Check the output of your function (1 line)


Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [155]:
# <20 lines
s = requests.Session()

def get__leaders():
  root_url = "https://country-leaders.herokuapp.com"
  
  cookie_url = root_url + "/cookie"
  cookies = requests.get(cookie_url).cookies

  countries_url = root_url + "/countries"
  req_countries = requests.get (countries_url, cookies=cookies)
  countries = req_countries.json()
  
  leaders_url = root_url + "/leaders"
  leaders_per_country ={}

  for country in countries:
     payload = {'country':country}
     req_leaders = requests.get(leaders_url, params=payload, cookies=cookies)
     leaders_per_country[country] = req_leaders.json()
     
     if req_leaders.status_code ==403:
           cookies = requests.get(cookie_url).cookies
           req_leaders = requests.get(leaders_url, params=payload, cookies=cookies)
     leaders = req_leaders.json()
      
     for leader in leaders:
            leader["first_paragraph"] = get_first_paragraph(leader["wikipedia_url"])
     leaders_per_country[country] = leaders
      
     return leaders_per_country

Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [159]:
# 22 lines
def get_leaders():
    root_url = "https://country-leaders.herokuapp.com"
    s = requests.Session()

    cookie_url = root_url + "/cookie"
    cookies = s.get(cookie_url).cookies

    countries_url = root_url + "/countries"
    req_countries = s.get (countries_url, cookies=cookies)
    countries = req_countries.json()

    leaders_url = root_url + "/leaders"
    leaders_per_country ={}
    for country in countries:
        payload = {'country':country}
        req_leaders = s.get(leaders_url, params=payload, cookies=cookies)

        if req_leaders.status_code == 403:
            cookies = s.get(cookie_url).cookies
            req_leaders = s.get(leaders_url, params=payload, cookies=cookies)
        leaders_per_country[country] = req_leaders.json()

        for leader in leaders_per_country[country]:
            leader["first_paragraph"] = get_first_paragraph(leader["wikipedia_url"], s)

    return leaders_per_country

Test your new functions.



In [160]:
%%time
get_leaders()


https://nl.wikipedia.org/wiki/Guy_Verhofstadt
https://nl.wikipedia.org/wiki/Yves_Leterme
https://nl.wikipedia.org/wiki/Herman_Van_Rompuy
https://nl.wikipedia.org/wiki/L%C3%A9on_Delacroix
https://nl.wikipedia.org/wiki/Henri_Carton_de_Wiart
https://nl.wikipedia.org/wiki/Georges_Theunis
https://nl.wikipedia.org/wiki/Aloys_Van_de_Vyvere
https://nl.wikipedia.org/wiki/Prosper_Poullet
https://nl.wikipedia.org/wiki/Henri_Jaspar
https://nl.wikipedia.org/wiki/Jules_Renkin
https://nl.wikipedia.org/wiki/Paul_van_Zeeland
https://nl.wikipedia.org/wiki/Achiel_Van_Acker
https://nl.wikipedia.org/wiki/Camille_Huysmans
https://nl.wikipedia.org/wiki/Gaston_Eyskens
https://nl.wikipedia.org/wiki/Leo_Tindemans
https://nl.wikipedia.org/wiki/Elio_Di_Rupo
https://nl.wikipedia.org/wiki/Jean-Luc_Dehaene
https://nl.wikipedia.org/wiki/Frans_Schollaert
https://nl.wikipedia.org/wiki/Pieter_de_Decker
https://nl.wikipedia.org/wiki/Paul-Henri_Spaak
https://nl.wikipedia.org/wiki/Auguste_Beernaert
https://nl.wikipedia.org

{'be': [{'id': 'Q12978',
   'first_name': 'Guy',
   'last_name': 'Verhofstadt',
   'birth_date': '1953-04-11',
   'death_date': None,
   'place_of_birth': 'Dendermonde',
   'wikipedia_url': 'https://nl.wikipedia.org/wiki/Guy_Verhofstadt',
   'start_mandate': '1999-07-12',
   'end_mandate': '2008-03-20',
   'first_paragraph': 'Guy Maurice Marie-Louise Verhofstadt )  is een Belgisch politicus voor de Open Vlaamse Liberalen en Democraten . Hij was premier van België van 12 juli 1999 tot 20 maart 2008 in drie regeringen. Nu is hij lid van het Europees Parlement, waar hij van 2009 tot 2019 fractieleider van de Alliantie van Liberalen en Democraten voor Europa  was.\n'},
  {'id': 'Q12981',
   'first_name': 'Yves',
   'last_name': 'Leterme',
   'birth_date': '1960-10-06',
   'death_date': None,
   'place_of_birth': 'Wervik',
   'wikipedia_url': 'https://nl.wikipedia.org/wiki/Yves_Leterme',
   'start_mandate': '2009-11-25',
   'end_mandate': '2011-12-06',
   'first_paragraph': 'Yves Camille Dé

Using a Session makes the first call to `get_leaders()` faster however, for technical reasons, the `@lru_cache` decorator no longer works. 

Problem: The `session` parameter is not *hashable* and since the cache is a dictionary using all the parameters as key, this poses a problem.

Solution: Create our own cache that only cares about the url.

The code for this is provided. You should only read it.

In [ ]:
cache = {}
def hashable_cache(f):
    def inner(url, session):
        if url not in cache:
            cache[url] = f(url, session)
        return cache[url]
    return inner

Overwrite the `get_first_paragraph()` function to use the new decorator like this: `@hashable_cache`.


In [ ]:
# <20 lines

Check that the cache is working again.

In [ ]:
# Just run it.
%%time
leaders_per_country = get_leaders()

## Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Make a tour in our [file handling section](../../2.python/2.python_advanced/04.File-handling/file_handling.ipynb) to know more about how to read and write files using Python.

In [161]:
# 3 lines
import json
with open('leaders.json','w') as f:
    json.dump(leaders_per_country,f)


Make sure the file can be read back. Write the code to read the file.

In [162]:
#3 lines
with open('leaders.json') as f:
    leaders = json.load(f)

Make a function `save()` to call this code easily.

In [164]:
# 3 lines
def save(leaders_per_country):
    with open('leaders.json','w') as f:
        json.dump(leaders_per_country, f)


In [165]:
# Call the function (1 line)
save(leaders_per_country)


## Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## To go further

If you want to practice scraping, you can read this section and tackle the exercise.

You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!